In [0]:
%run "../includes/configuration"

In [0]:
%run "../includes/common_functions"

In [0]:
dbutils.widgets.text("p_data_source", "")
v_data_source = dbutils.widgets.get("p_data_source")

In [0]:
dbutils.widgets.text("p_file_date", "2021-03-28")
v_file_date = dbutils.widgets.get("p_file_date")

In [0]:
from pyspark.sql.types import StructType, StructField, IntegerType, StringType, FloatType

In [0]:
results_schema = StructType(fields=[StructField("resultId", IntegerType(), False),
                                    StructField("raceId", IntegerType(), True),
                                    StructField("driverId", IntegerType(), True),
                                    StructField("constructorId", IntegerType(), True),
                                    StructField("number", IntegerType(), True),
                                    StructField("grid", IntegerType(), True),
                                    StructField("position", IntegerType(), True),
                                    StructField("positionText", StringType(), True),
                                    StructField("positionOrder", IntegerType(), True),
                                    StructField("points", FloatType(), True),
                                    StructField("laps", IntegerType(), True),
                                    StructField("time", StringType(), True),
                                    StructField("milliseconds", IntegerType(), True),
                                    StructField("fastestLap", IntegerType(), True),
                                    StructField("rank", IntegerType(), True),
                                    StructField("fastestLapTime", StringType(), True),
                                    StructField("fastestLapSpeed", FloatType(), True),
                                    StructField("statusId", StringType(), True)])

In [0]:
results_df = spark.read \
.schema(results_schema) \
.json(f"{incraw_folder_path}/{v_file_date}/results.json")

In [0]:

from pyspark.sql.functions import lit

In [0]:
results_with_columns_df = results_df.withColumnRenamed("resultId", "result_id") \
                                    .withColumnRenamed("raceId", "race_id") \
                                    .withColumnRenamed("driverId", "driver_id") \
                                    .withColumnRenamed("constructorId", "constructor_id") \
                                    .withColumnRenamed("positionText", "position_text") \
                                    .withColumnRenamed("positionOrder", "position_order") \
                                    .withColumnRenamed("fastestLap", "fastest_lap") \
                                    .withColumnRenamed("fastestLapTime", "fastest_lap_time") \
                                    .withColumnRenamed("fastestLapSpeed", "fastest_lap_speed") \
                                    .withColumn("data_source", lit(v_data_source)) \
                                    .withColumn("file_date", lit(v_file_date))

In [0]:
results_with_ingestion_date_df = add_ingestion_date(results_with_columns_df)

In [0]:
from pyspark.sql.functions import col

In [0]:
results_final_df = results_with_ingestion_date_df.drop(col("statusId"))

In [0]:
results_deduped_df = results_final_df.dropDuplicates(["race_id","driver_id"])

In [0]:
merge_condition = "tgt.result_id = src.result_id AND tgt.race_id = src.race_id"
merge_delta_data(results_deduped_df,'f1_inc_processed', 'results_dt',incprocessed_folder_path, merge_condition,'race_id')

In [0]:
%sql
select * from f1_inc_processed.results_dt

result_id race_id driver_id constructor_id number grid position position_text position_order points laps time milliseconds fastest_lap rank fastest_lap_time fastest_lap_speed data_source file_date ingestion_date 20677 351 1 1 2 3 null R 19 0.0 35 \N null 31 10 1:50.750 164.901 ergest_api 2021-03-21 2024-12-21T02:01:22.457Z 20676 351 2 15 22 14 null R 18 0.0 36 \N null 29 16 1:52.475 162.372 ergest_api 2021-03-21 2024-12-21T02:01:22.457Z 20663 351 3 131 4 7 5 5 5 10.0 61 +49.394 7122973 55 8 1:50.125 165.837 ergest_api 2021-03-21 2024-12-21T02:01:22.457Z 20659 351 4 6 8 1 1 1 1 25.0 61 1:57:53.579 7073579 58 1 1:47.976 169.137 ergest_api 2021-03-21 2024-12-21T02:01:22.457Z 20674 351 5 205 19 19 16 16 16 0.0 58 \N null 53 18 1:53.051 161.544 ergest_api 2021-03-21 2024-12-21T02:01:22.457Z 20665 351 9 4 11 8 7 7 7 6.0 61 +1:26.559 7160138 56 3 1:49.255 167.157 ergest_api 2021-03-21 2024-12-21T02:01:22.457Z 20675 351 10 166 24 18 null R 17 0.0 49 \N null 38 19 1:53.559 160.822 ergest_api 2021-03-21 2024-12-21T02:01:22.457Z 20666 351 13 6 7 24 8 8 8 4.0 61 +1:53.297 7186876 45 12 1:52.079 162.945 ergest_api 2021-03-21 2024-12-21T02:01:22.457Z 20681 351 15 205 18 21 null R 23 0.0 27 \N null 20 21 1:56.386 156.915 ergest_api 2021-03-21 2024-12-21T02:01:22.457Z 20667 351 16 10 14 15 9 9 9 2.0 61 +2:02.416 7195995 45 15 1:52.473 162.374 ergest_api 2021-03-21 2024-12-21T02:01:22.457Z 20662 351 18 1 1 4 4 4 4 12.0 61 +30.384 7103963 61 7 1:49.711 166.462 ergest_api 2021-03-21 2024-12-21T02:01:22.457Z 20660 351 20 9 5 2 2 2 2 18.0 61 +0.293 7073872 59 2 1:48.141 168.879 ergest_api 2021-03-21 2024-12-21T02:01:22.457Z 20682 351 24 10 15 16 null R 24 0.0 1 \N null null null \N null ergest_api 2021-03-21 2024-12-21T02:01:22.457Z 20671 351 30 131 3 9 13 13 13 0.0 60 \N null 54 4 1:49.680 166.509 ergest_api 2021-03-21 2024-12-21T02:01:22.457Z 20678 351 32 164 20 22 null R 20 0.0 31 \N null 23 22 1:57.766 155.077 ergest_api 2021-03-21 2024-12-21T02:01:22.457Z 20672 351 67 5 16 13 14 14 14 0.0 60 \N null 59 6 1:49.710 166.464 ergest_api 2021-03-21 2024-12-21T02:01:22.457Z 20679 351 155 15 23 10 null R 21 0.0 30 \N null 22 20 1:53.957 160.26 ergest_api 2021-03-21 2024-12-21T02:01:22.457Z 20668 351 807 3 10 17 10 10 10 1.0 61 +2:12.791 7206370 45 13 1:52.213 162.751 ergest_api 2021-03-21 2024-12-21T02:01:22.457Z 20673 351 810 166 25 20 15 15 15 0.0 59 \N null 55 17 1:52.513 162.317 ergest_api 2021-03-21 2024-12-21T02:01:22.457Z 20680 351 811 164 21 23 null R 22 0.0 29 \N null 19 23 1:57.962 154.819 ergest_api 2021-03-21 2024-12-21T02:01:22.457Z 1102 69 2 2 16 9 8 8 8 1.0 53 +1:16.095 5108508 31 13 1:34.525 221.16 ergest_api 2021-03-21 2024-12-21T02:01:22.457Z 1095 69 4 4 1 5 1 1 1 10.0 53 1:23:52.413 5032413 14 1 1:32.676 225.572 ergest_api 2021-03-21 2024-12-21T02:01:22.457Z 1103 69 9 2 17 12 9 9 9 0.0 53 +1:16.932 5109345 39 6 1:33.509 223.563 ergest_api 2021-03-21 2024-12-21T02:01:22.457Z 1096 69 13 6 6 1 2 2 2 8.0 53 +16.151 5048564 37 3 1:33.296 224.073 ergest_api 2021-03-21 2024-12-21T02:01:22.457Z 1115 69 14 9 14 17 null R 21 0.0 35 \N null 20 16 1:35.052 219.934 ergest_api 2021-03-21 2024-12-21T02:01:22.457Z 1100 69 15 7 8 4 6 6 6 3.0 53 +46.717 5079130 2 9 1:33.866 222.713 ergest_api 2021-03-21 2024-12-21T02:01:22.457Z 1113 69 17 3 9 14 null R 19 0.0 39 \N null 19 18 1:35.092 219.841 ergest_api 2021-03-21 2024-12-21T02:01:22.457Z 1098 69 18 11 12 7 4 4 4 5.0 53 +34.101 5066514 35 5 1:33.451 223.702 ergest_api 2021-03-21 2024-12-21T02:01:22.457Z 1106 69 22 11 11 8 12 12 12 0.0 52 \N null 40 10 1:34.071 222.227 ergest_api 2021-03-21 2024-12-21T02:01:22.457Z 1101 69 23 7 7 3 7 7 7 2.0 53 +48.869 5081282 2 8 1:33.607 223.329 ergest_api 2021-03-21 2024-12-21T02:01:22.457Z 1108 69 24 5 20 15 14 14 14 0.0 52 \N null 22 12 1:34.131 222.086 ergest_api 2021-03-21 2024-12-21T02:01:22.457Z 1112 69 26 5 21 19 18 18 18 0.0 48 \N null 37 14 1:34.560 221.078 ergest_api 2021-03-21 2024-12-21T02:01:22.457Z 1116 69 27 14 19 16 null R 22 0.0 20 \N null 19 22 1

In [0]:
%sql
select count(*) from f1_inc_processed.results_dt

count(1) 24909

In [0]:
dbutils.notebook.exit("Success")

In [0]:
 %sql
SELECT race_id, driver_id, COUNT(1) 
FROM f1_inc_processed.results_dt
GROUP BY race_id, driver_id
HAVING COUNT(1) > 1
ORDER BY race_id, driver_id DESC;

race_id driver_id count(1)

In [0]:
%sql
SELECT race_id, COUNT(1) 
FROM f1_inc_processed.results_dt
GROUP BY race_id
ORDER BY race_id DESC;

race_id count(1) 1053 20 1052 20 1047 20 1046 20 1045 20 1044 20 1043 20 1042 20 1041 20 1040 20 1039 20 1038 20 1037 20 1036 20 1035 20 1034 20 1033 20 1032 20 1031 20 1030 20 1029 20 1028 20 1027 20 1026 20 1025 20 1024 20 1023 20 1022 20 1021 20 1020 20 1019 20 1018 20 1017 20 1016 20 1015 20 1014 20 1013 20 1012 20 1011 20 1010 20 1009 20 1008 20 1007 20 1006 20 1005 20 1004 20 1003 20 1002 20 1001 20 1000 20 999 20 998 20 997 20 996 20 995 20 994 20 993 20 992 20 991 20 990 20 989 20 988 20 987 20 986 20 985 20 984 20 983 20 982 20 981 20 980 20 979 20 978 20 977 20 976 20 975 20 974 20 973 20 972 20 971 20 970 20 969 20 968 22 967 22 966 22 965 22 964 22 963 22 962 22 961 22 960 22 959 22 958 22 957 22 956 22 955 22 954 22 953 22 952 22 951 22 950 22 949 22 948 22 945 20 944 20 943 20 942 20 941 20 940 20 939 20 938 20 937 20 936 20 934 20 933 20 932 20 931 20 930 20 929 20 928 20 927 20 926 18 918 20 917 18 916 18 915 21 914 22 913 22 912 22 911 22 910 22 909 22 908 22 907 22 906 22 905 22 904 22 903 22 902 22 901 22 900 22 899 22 898 22 897 22 896 22 895 22 894 22 893 22 892 22 891 22 890 22 888 22 887 22 886 22 885 22 884 22 883 22 882 22 881 22 880 22 879 24 878 24 877 24 876 24 875 24 874 24 873 24 872 24 871 24 870 24 869 24 868 24 867 24 866 24 865 24 864 24 863 24 862 24 861 24 860 24 859 24 858 24 857 24 856 24 855 24 854 24 853 24 852 24 851 24 850 24 849 24 848 24 847 24 846 24 845 24 844 24 843 24 842 24 841 24 839 27 838 19 837 14 836 18 835 34 834 21 833 23 832 20 831 22 830 22 829 20 828 23 827 13 826 34 825 21 824 35 823 18 822 30 821 32 820 21 819 22 818 33 817 21 816 31 815 20 814 34 813 27 812 25 811 20 810 19 809 37 808 17 807 23 806 21 805 17 804 23 803 33 802 22 801 14 800 42 799 18 798 23 797 26 796 16 795 16 794 35 793 24 792 22 791 26 790 22 789 28 788 19 787 15 786 34 785 19 784 15 783 19 782 16 781 24 780 19 779 15 778 33 777 21 776 16 775 25 774 21 773 15 772 26 771 20 770 21 769 19 768 33 767 18 766 30 765 10 764 19 763 21 762 16 761 15 760 30 759 22 758 15 757 33 756 24 755 23 754 17 753 15 752 25 751 23 750 19 749 21 748 33 747 24 746 22 745 20 744 39 743 33 742 31 741 31 740 26 739 17 738 21 737 21 736 20 735 31 734 31 733 25 732 22 731 26 730 24 729 22 728 23 727 25 726 24 725 33 724 29 723 26 722 24 721 21 720 24 719 25 718 19 717 19 716 24 715 20 714 23 713 25 712 17 711 18 710 18 709 23 708 19 707 18 706 23 705 21 704 17 703 23 702 17 701 19 700 17 699 31 698 18 697 19 696 22 695 19 694 17 693 20 692 17 691 18 690 16 689 19 688 18 687 18 686 18 685 24 684 21 683 15 682 18 681 17 680 19 679 18 678 21 677 20 676 21 675 22 674 20 673 20 672 17 671 19 670 18 669 18 668 14 667 23 666 17 665 18 664 20 663 15 662 14 661 17 660 13 659 15 658 16 657 14 656 18 655 18 654 27 653 20 652 27 651 24 650 25 649 23 648 23 647 24 646 17 645 21 644 22 643 23 642 29 641 26 640 24 639 22 638 23 637 24 636 23 635 23 634 22 633 22 632 25 631 31 630 24 629 27 628 25 627 27 626 26 625 25 624 25 623 25 622 26 621 26 620 22 619 28 618 26 617 25 616 23 615 22 614 24 613 29 612 25 611 21 610 25 609 23 608 22 607 25 606 20 605 19 604 30 603 30 602 31 601 31 600 32 599 34 598 30 597 27 596 27 595 28 594 32 593 27 592 27 591 25 590 25 589 24 588 28 587 30 586 26 585 28 584 26 583 25 582 26 581 24 580 26 579 26 578 28 577 23 576 23 575 26 574 27 573 27 572 29 571 27 570 25 569 28 568 30 567 30 566 27 565 25 564 29 563 30 562 27 561 25 560 22 559 23 558 27 557 27 556 34 555 34 554 30 553 29 552 36 551 30 550 31 549 31 548 26 547 31 546 22 545 23 544 22 543 21 542 28 541 27 540 31 539 33 538 31 537 30 536 30 535 29 534 27 533 29 532 30 531 30 530 30 529 30 528 28 527 27 526 30 525 30 524 28 523 26 522 26 521 26 520 26 519 27 518 25 517 28 516 27 515 26 514 26 513 26 512 26 511 27 510 28 509 28 508 29 507 26 506 26 505 27 504 27 503 27 502 27 501 27 500 28 499 28 498 28 497 30 496 30 495 30 494 30 493 28 492 30 491 30 490 29 489 30 488 31 487 31 486 32 485 29 484 30 483 29 482 30 481 30 480 29 479 29 478 29 477 29 476 30